In [14]:
# Perform 3C STA-LTA detection for all time windows and a list of stations

In [15]:
## Import modules

from os.path import join, exists
from os import makedirs
from shutil import rmtree
from obspy import read
from obspy.signal.trigger import coincidence_trigger
from datetime import datetime
from pandas import DataFrame, Int64Dtype, to_datetime, read_csv
from numpy import nan
from time import time
from utils_preproc import preprocess_stream
from utils_sta_lta import run_sta_lta, get_snr

In [16]:
## Inputs

### Corner frequencies for filtering the data
freqmin = 10.0
freqmax = 450.0

### STA-LTA parameters
sta = 0.01
lta = 0.2
thr_on = 7
thr_off = 2

### Paramters for computing the signal-to-noise ratio
snrflag = False
snrwin = 0.02

### Root directory name
root = "/Volumes/OmanData/geophones_no_prefilt/data"


In [17]:
## Read the time-window and station lists

### Read the time-window list
inpath = join(root, "time_windows.csv")
twindf = read_csv(inpath,  date_format="%Y-%m-%d-%H-%M-%S")

### Read the station list
inpath = join(root, "stations_sta_lta.csv")
stadf = read_csv(inpath, index_col=0)

In [18]:
## Create the output directory
outdir = join(root, f"detections_sta{sta:.2f}s_lta{lta:.2f}s_on{thr_on:d}_off{thr_off:d}")

if exists(outdir):
    rmtree(outdir)
    print(f"Removed existing directory {outdir}")

makedirs(outdir)
print(f"Created directory {outdir} for the output")

Removed existing directory /Volumes/OmanData/geophones_no_prefilt/data/detections_sta0.01s_lta0.20s_on5_off2
Created directory /Volumes/OmanData/geophones_no_prefilt/data/detections_sta0.01s_lta0.20s_on5_off2 for the output


In [19]:
## Initialize the dataframe for the hourly detection numbers
detnumdf = DataFrame(nan, index=twindf["name"], columns=stadf["name"])
detnumdf.index.name = "hour"

In [20]:
## Loop over stations
for station in stadf["name"]:
    runtime_b = time()
    detections = []

    print(f"Start working on {station}...")
    starttime_run = time()

    ### Loop over time windows
    for timewin in twindf["name"]:
        print(f"Working on {station} for {timewin}...")
        indir = join(root, timewin)

        #### Read and filter the 3C data
        pattern = f"*{station}*{timewin}*SAC"
        inpath = join(indir, pattern)

        try:
            stream = read(inpath)
        except:
            print("The SAC files do not exist! Skipped.")
            continue

        stream = preprocess_stream(stream, freqmin, freqmax)

        #### Perform STA-LTA detection for the stream
        triggers = run_sta_lta(stream, sta, lta, thr_on, thr_off, thr_coincidence_sum=2, trigger_type='classicstalta')     

        #### Compute the SNR for each detection and save the detection information to a dictionary

        for i, trigger in enumerate(triggers):
            ##### Get the trigger and detrigger time
            trigger_time = to_datetime(trigger['time'].datetime)
            detrigger_time = trigger['time']+trigger['duration']
            detrigger_time = to_datetime(detrigger_time.datetime)

            ##### Compute the SNR for the detection
            if snrflag:
                print("Computing the SNR for each detection...")
                snr = get_snr(trigger, stream, snrwin)

                detections.append({'trigger_time':trigger_time, 'detrigger_time':detrigger_time, 'signal_noise_ratio':snr})
            else:
                detections.append({'trigger_time':trigger_time, 'detrigger_time':detrigger_time})

        #### Save the number of detections to the detection number DataFrame
        detnumdf.loc[timewin, station] = len(triggers)

    ### Convert the list of dictionaries to a DataFrame
    detections = DataFrame(detections)
    numdet = len(detections)

    ### Record the time
    endtime_run = time()
    dur = (endtime_run-starttime_run)/60

    print(f"{station} is finished.")
    print(f"It took {dur:.2f} minutes to finish.")
    print(f"Total number of detections: {numdet}")

    ### Save the DataFrame to a CSV file
    if numdet > 0:
        outpath = join(outdir, f"{station}.csv")
        detections.to_csv(outpath, date_format="%Y-%m-%dT%H:%M:%S.%fZ")
        print(f"Saving the detection information to {outpath}...")

## Save the hourly detection numbers to a CSV file
detnumdf.index = to_datetime(detnumdf.index, format="%Y-%m-%d-%H-%M-%S")
detnumdf = detnumdf.astype(Int64Dtype())
outpath = join(outdir, "hourly_detection_numbers.csv")
detnumdf.to_csv(outpath)
print(f"Saved the hourly detection numbers to {outpath}")

Start working on A01...
Working on A01 for 2020-01-10-11-00-00...


Eliminating repeating events...
Finished.
Number of detections: 1435. Number of repeating detections removed: 218.
Working on A01 for 2020-01-10-12-00-00...
Eliminating repeating events...
Finished.
Number of detections: 2631. Number of repeating detections removed: 528.
Working on A01 for 2020-01-10-13-00-00...
Eliminating repeating events...
Finished.
Number of detections: 1671. Number of repeating detections removed: 399.
Working on A01 for 2020-01-10-14-00-00...
Eliminating repeating events...
Finished.
Number of detections: 947. Number of repeating detections removed: 209.
Working on A01 for 2020-01-10-15-00-00...
Eliminating repeating events...
Finished.
Number of detections: 106. Number of repeating detections removed: 4.
Working on A01 for 2020-01-10-16-00-00...
Eliminating repeating events...
Finished.
Number of detections: 159. Number of repeating detections removed: 13.
Working on A01 for 2020-01-10-17-00-00...
Eliminating repeating events...
Finished.
Number of detections: 